 ## Simulations of the BSC and Rep(3)

### Simulating the BSC

*Note*.The PyM function `rd_float`() yiels a random float number in the interval $[0,1]$ drawn uniformly.


In [2]:
from PyM import rd_float
 
[rd_float() for _ in range(5)]
        

[0.03630002031321555,
 0.40492654125689354,
 0.12471127720739272,
 0.9583077833739496,
 0.02586925167831622]

The function`BSC(x,p)` takes a string of bits $x$ and produces another
string of bits $y$ of the same length by flipping each bit $b$ in $x$ according to the probability $p$. This is accomplished by generatig a random value $r\in [0,1]$ and flipping $b$ if and only if $r\le p$.

*Note.* The function `hd(x,y)` gives the number of positions in which two binary strings of the same length, $x$ and $y$, are different (*Hamming distance*).


In [3]:
from PyM import hd

def BSC(x,p):
    y = ''
    for b in x:
        r = rd_float()
        if r<=p: 
            if b=='0': y += '1'
            else: y += '0'
        else: y += b
    return y

x = '0101010101'
# The expected number of flips is 10*0.2 = 2
y = BSC(x,0.2) 

print(x,y,hd(x,y))

# The expected number of flips is 50*0.1 = 5
print(BSC(50*'0',0.1))

0101010101 0101010101 0
10010000000000000000000100000000001000101000000000


### Encoding with the Rep(3) code

In [4]:
def rep3enc(u):
    x = ''
    for b in u:
        x += 3*b
    return x

print(rep3enc('0'))
print(rep3enc('1'))
print(rep3enc('01110011'))

000
111
000111111111000000111111


### Decoding by the Rep(3) code

In [5]:
def rep3dec(y):
    u = ''
    while len(y)>2:
        c = y[:3] # first 3 bits of y
        y = y[3:] # remainder string
        if c.count('1')>1:
            u += '1'
        else: u += '0'
    if y=='':
        return u
    print('rep3dec stopped at undecodable tail', y)
    return u

x = '000111111111000000111111'
y = BSC(x,0.2)
print(y)

u = rep3dec(y)
print(u)

001111011111000000011101
01110011


### Testing the BSC simulation and the performance of Rep(3)

A binary string $u$ is encoded using the Rep(3) code. Then it is sent trough the BSC with bit-error probability $p$, and the received vector, $y$, is decoded by the Rep(3) decoder, obtaining a vector $v$. The function `rep3test(u,p)` returns the triple $(E,Ec,m)$, where $E$ is the expected number of errors without coding, $Ec$ is the expected number of errors using coding, and $m$ is the number of actual errors using coding. 

In [6]:
def rep3test(u,p):
    x = rep3enc(u)
    y = BSC(x,p)
    v= rep3dec(y)
    E = len(u)*p
    Ec= len(u)*(3*p**2*(1-p)+p**3)  
    m = hd(u,v)                    
    return (E, round(Ec,3), m)

#### Example

Let $L=100000$ and $u$ be the binary string `L*'0'` (a string of $L$ zeros). For $p = 0.005$, we have $E = 500$ and $Ec =L[3p^2(1-p)+p^3]= 7.475$. Thus the value of $m$ is expected to fluctuate about $Ec$ when the test is repeated. Note that the approximation $3p$ of the reduction factor is 0.015, which gives an expectation of 7.5 errors.  

In [7]:
L = 100000; p = 0.005
print(rep3test(L*'0',p))

(500.0, 7.475, 9)


#### Remarks
Under the conditions of the above example, the probability $p_m$ of getting $m$ errors in a trial is $\binom{L}{m}{p'}^m(1-p')^{L-m}$, $p'=3p^2(1-p)+p^3$. This *Bernoulli expression* can be well approximated by the *Poisson distribution* $e^{-\lambda}\lambda^m/m!$, $\lambda = Lp'= 7.475$, which means that the $p_m$ are proportional to $\lambda^m/m!$ with scaling factor
$K=e^{\lambda}$.

Next computation shows that the $p_m$ increase from $m=0$ up to $m=7$ and then decrease. Moreover, the chances that $m\le 7$ are slightly higher than the chances of getting $m>7$
(the odds are 53 to 47). The figures also show that the values of $m$ are rather scattered
around $m=7$. For instance, the value of $m$ falls 
42% of times within the interval $[6,8]$,
65% within $[5,9]$,
80% within $[4,10]$, 
90% within $[3,11], and so on. 

In [8]:
l = 7.475
from PyM import factorial
P = [(m,l**m/factorial(m)) for m in range(19)]
P = [(p[0],round(p[1],1)) for p in P]
print(P)

from math import exp
K = round(exp(l),1)
print(K)

K_low = round(sum([P[m][1] for m in range(8)]),1)

print(K_low)

p_low = round(K_low/K,2)

print(p_low)

print(1-p_low)

[(0, 1.0), (1, 7.5), (2, 27.9), (3, 69.6), (4, 130.1), (5, 194.5), (6, 242.3), (7, 258.7), (8, 241.8), (9, 200.8), (10, 150.1), (11, 102.0), (12, 63.5), (13, 36.5), (14, 19.5), (15, 9.7), (16, 4.5), (17, 2.0), (18, 0.8)]
1763.4
931.6
0.53
0.47


In [9]:
dm = 2
K_around= round(sum([P[m][1] for m in range(7-dm,8+dm)]),1)
print(K_around)
P_around = round(K_around/K,2)
print(P_around)

1138.1
0.65
